###  Download the HK population statistic by census 2016

In [68]:
import pandas as pd
df_source=pd.read_csv('https://www.bycensus2016.gov.hk/data/DCCA_16BC.zip')
df_source.head(10)

區議會分區 （分組)  ...                   按5年前居住地區劃分的並無作內部遷移(20)的5歲及以上人口.2
0  District Council district (class)  ...  Population aged 5 and over not having internal...
1                         區議會分區 （分組)  ...                                           居於香港以外地方
2  District Council district (class)  ...               Place of residence outside Hong Kong
3                           dc_class  ...                                             pm_out
4                                  A  ...                                               1770
5                                  A  ...                                               2907
6                                  A  ...                                               2828
7                                  A  ...                                               3489
8                                  A  ...                                               2174
9                                  A  ...                                               1412

[10 rows x 214 columns]

### Download the geojson data of HK based on District Counsel in 2015

In [69]:
!wget --quiet https://raw.githubusercontent.com/waitse/Coursera_Capstone/main/HK_2015.geojson

### Download the 27 locations chosen from the user for finding the top three locations

In [70]:
df_a=pd.read_excel('https://raw.githubusercontent.com/waitse/Coursera_Capstone/main/Address.xlsx')
df_a['Address']
df_a['Code']
df_a['lat']=0
df_a['lng']=0
df_a.set_index('Code', drop = False, inplace = True)
df_a

Code                                            Address  lat  lng
Code                                                                   
BE1    BE1                   4 Babington Path, Mid Levels, HK    0    0
BE2    BE2                    33 Marble Road, North Point, HK    0    0
BE3    BE3                       1 On Chun Street, Ma On Shan    0    0
BE4    BE4              6 Tak Hong Street, Hung Hom, Kowloon.    0    0
BE5    BE5                  18 Pui Shing Road, Tseung Kwan O     0    0
BE6    BE6      Broadway, Phase 1  Mei Foo Sun Chuen, Kowloon    0    0
BE7    BE7                 3 On Kwan Street, Shek Mun, Shatin    0    0
BE8    BE8                 35 Tai Hong Street, Sai Wan Ho, HK    0    0
BE9    BE9               5-7 Fung Yau Street North, Yuen Long    0    0
BE10  BE10              18 Castle Peak Road Tam Mi, Yuen Long    0    0
BE11  BE11                               620 Castle Peak Road    0    0
BE12  BE12                      93 Cha Kwo Ling Road, Kowloon    0    0
BE13  BE13                88 O King Road, Tseung Kwan O, N.T.    0    0
BE14  BE14           8 Muk Lun Street, Wong Tai Sin, Kowloon.    0    0
BE15  BE15                    Amoy Plaza Phase I, Kowloon Bay    0    0
BE16  BE16          1 Tsun King Road, Shatin, New Territories    0    0
BE17  BE17                   100 Tai Ho Road, Tsuen Wan, N.T.    0    0
BE18  BE18            38 Cherry Street, Tai Kok Tsui, Kowloon    0    0
BE19  BE19            3 Ma Sik Road, Fanling, New Territories    0    0
BE20  BE20  202 Tin Sum Tsuen, Tai Wai, Sha Tin, New Terri...    0    0
BE21  BE21      No. 2, Tuen Hi Road Tuen Mun, New Territories    0    0
BE22  BE22   7-19 Tsing Luk Street, Tsing Yi, New Territories    0    0
BE23  BE23                         1 Kornhill Road, Hong Kong    0    0
BE24  BE24             18 Tong Chun Street, Tseung Kwan O, NT    0    0
BE25  BE25               12-18 Tin Yan Road, Tin Shui Wai, NT    0    0
BE26  BE26         863 Lai Chi Kok Road, Lai Chi Kok, Kowloon    0    0
BE27  BE27                      No. 1 On Tai Road, Tai Po, NT    0    0

### Define the function to look for the latitude and longitude of the specific address and generate a map to label the specific location

In [71]:
def print_locator(address, world_map, label, df_a):

  geolocator = Nominatim(user_agent="foursquare_agent")
  location = geolocator.geocode(address)
  lat = location.latitude
  lng = location.longitude
  print(label, lat, lng)
  df_a.loc[label,'lat']=lat
  df_a.loc[label,'lng']=lng

  # instantiate a feature group for the incidents in the dataframe
  incidents = folium.map.FeatureGroup()

  incidents.add_child(
      folium.CircleMarker(
          [lat, lng],
          radius=5, # define how big you want the circle markers to be
          color='yellow',
          fill=True,
          fill_color='blue',
          fill_opacity=0.6
      )
  )

  folium.Marker([lat, lng], popup=label).add_to(world_map)
  # add incidents to map
  world_map.add_child(incidents)

  return df_a
  

### Use print_locator function to generate the map with labels

In [72]:
import folium
df=df_source.loc[:]
df.columns=df.loc[3]
df=df.loc[4:434]
df=df[['dcca_class','age_1']]
df.reset_index(inplace=True, drop=True)
df.head()
df.columns=['CACODE','PopulationUnder15']
df.shape

import numpy as np
df['PopulationUnder15'] = df['PopulationUnder15'].astype(np.int64)
df.tail()

world_map = folium.Map(location=[22.302711, 114.177216], zoom_start=11)

#world_geo = r'DCCA2019.json'
world_geo = r'HK_2015.geojson'

world_map.choropleth(
    geo_data=world_geo,
    data=df,
    columns=['CACODE','PopulationUnder15'],
    key_on='properties.CACODE',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Poupulation under age 15 in Hong Kong in 2016',
    reset=True
)

from geopy.geocoders import Nominatim
addresses = df_a['Address']
labels=df_a['Code']

for address, label, in zip(addresses, labels):
  df_a=print_locator(address, world_map, label, df_a)

world_map

/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


BE1 22.2832693 114.1410404
BE2 22.2920468 114.2015201
BE3 22.4272691 114.23554625
BE4 22.3066369 114.1896261
BE5 22.3145915 114.265232
BE6 22.3354854 114.1413785
BE7 22.388005 114.2074498
BE8 22.2831425 114.2215567
BE9 22.4435426 114.0334655
BE10 22.4687338 114.0543833
BE11 22.3370842 114.1422362
BE12 22.2990416 114.2319545
BE13 22.3010314 114.2514214
BE14 22.3409129 114.1967937
BE15 22.32407865 114.21647771517283
BE16 22.3989882 114.2007163
BE17 22.367351 114.1109787
BE18 22.317876 114.1611461
BE19 22.5019797 114.1408483
BE20 22.4344044 113.9926623
BE21 22.3929907 113.9769965
BE22 22.3551291 114.1038976
BE23 22.2845316 114.2163521
BE24 22.3063116 114.2614418
BE25 22.4597955 114.0017568
BE26 22.334841 114.1463021
BE27 22.4534552 114.1706956


### The dataframe with latitude and longtitude is also returned from the print_locator function

In [73]:
df_a.head()

Code                                Address        lat         lng
Code                                                                   
BE1   BE1       4 Babington Path, Mid Levels, HK  22.283269  114.141040
BE2   BE2        33 Marble Road, North Point, HK  22.292047  114.201520
BE3   BE3           1 On Chun Street, Ma On Shan  22.427269  114.235546
BE4   BE4  6 Tak Hong Street, Hung Hom, Kowloon.  22.306637  114.189626
BE5   BE5      18 Pui Shing Road, Tseung Kwan O   22.314591  114.265232

### Define the variable for foursquare API and define the function for the URL

In [74]:
CLIENT_ID = 'TSMWDNP1OUVXHLK1LVDZV2XKU2J2LDQDQDUNMHUN2NMKJSMC' # your Foursquare ID
CLIENT_SECRET = 'TJEDZRYM30MPNYC3PPKDVNUUGV0XML11PY2KQJK5JGEAGQGC' # your Foursquare Secret
# ACCESS_TOKEN = '4PRFKBUALZZZBYN5WED122EF2PYZNGSXLTHOM3E3T0RYXA2D' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 500
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

def get_explorer_a_location_with_categoryId_url(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT, CategoryId):
    return 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&categoryId={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT, CategoryId)


Your credentails:
CLIENT_ID: TSMWDNP1OUVXHLK1LVDZV2XKU2J2LDQDQDUNMHUN2NMKJSMC
CLIENT_SECRET:TJEDZRYM30MPNYC3PPKDVNUUGV0XML11PY2KQJK5JGEAGQGC


### use the get_explorer_a_location_with_categoryId_url to obtain the nearby nursery school venues

In [75]:
import requests # library to handle requests

### Define get_category_type function

In [76]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

### Define get_nearby_venus_for_code function to obtain the number of nursery schools around the specific location

In [77]:
def get_nearby_venus_for_code(df_a, code):
  neighborhood_latitude=df_a['lat'][code]
  neighborhood_longitude=df_a['lng'][code]
  url=get_explorer_a_location_with_categoryId_url(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, 1000, LIMIT, '4f4533814b9074f6e4fb0107')
  results = requests.get(url).json()
  #df_n=get_nearby_venues(results)
  #df_n['Code']=code
  return results['response']['totalResults']

totalResults_List=[]
for code in df_a['Code']:
  totalResults=get_nearby_venus_for_code(df_a, code)
  totalResults_List.append(totalResults)

totalResults_List

[5,
 4,
 1,
 4,
 1,
 3,
 3,
 5,
 2,
 0,
 3,
 3,
 1,
 3,
 2,
 3,
 3,
 6,
 1,
 0,
 0,
 4,
 7,
 2,
 1,
 2,
 3]

### It shows the top 5 locations

In [78]:
details = { 
    'Code' : df_a['Code'].tolist(), 
    'Nursery_School_Count' : totalResults_List
} 

df_top5=pd.DataFrame(details).sort_values(by='Nursery_School_Count', ascending=False).head(5)
df_top5

Code  Nursery_School_Count
22  BE23                     7
17  BE18                     6
0    BE1                     5
7    BE8                     5
3    BE4                     4

### We want top 3 but BE1 and BE8 has the same number of nursury school.  We pick either of them by the population under age 15

In [79]:
df_top4=df_top5.head(4)
df_r=pd.read_excel('https://raw.githubusercontent.com/waitse/Coursera_Capstone/main/Address.xlsx')
df_r=df_r[df_r['Code'].isin(df_top4['Code'].tolist())]
df_r['lat']=0
df_r['lng']=0
df_r.set_index('Code', drop = False, inplace = True)

world_map_r = folium.Map(location=[22.302711, 114.177216], zoom_start=13)

world_map_r.choropleth(
    geo_data=world_geo,
    data=df,
    columns=['CACODE','PopulationUnder15'],
    key_on='properties.CACODE',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Poupulation under age 15 in Hong Kong in 2016',
    reset=True
)

addresses = df_r['Address']
labels=df_r['Code']

for address, label, in zip(addresses, labels):
  df_r=print_locator(address, world_map_r, label, df_r)


world_map_r

/usr/local/lib/python3.6/dist-packages/folium/folium.py:426: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


BE1 22.2832693 114.1410404
BE8 22.2831425 114.2215567
BE18 22.317876 114.1611461
BE23 22.2845316 114.2163521


### Since the district of BE8 has more population under 15 than that of BE1

## We recommend BE8, BE18, and BE23